# Aktienkurse abfragen

Bibliotheken importieren

In [1]:
import requests
import json
import pandas as pd
import numpy as np
import datetime
from bokeh.plotting import figure, show, output_notebook, reset_output
from bokeh.io import push_notebook, show, output_notebook
from bokeh.models import DatetimeTickFormatter
from bokeh.layouts import column as bokehcol
from math import pi

Api anfragen

In [2]:
API_URL = "https://www.alphavantage.co/query" 
symbol = "BMW.DE"

# Alle Parameter in der Dokumentation: https://www.alphavantage.co/documentation/#daily
params = { "function": "TIME_SERIES_DAILY", 
"symbol": symbol,
"outputsize" : "full",
"datatype": "json", 
"apikey": "68EYDDAAQ4ETZKE5" }

# HTML-Anfrage an die "API_URL" mit allen Parametern "params"
response = requests.get(API_URL, params)
# JSON aus Anfrage dekodieren in Variable "data"
data = response.json()
# Variable "data" zu einem Python-Dictionary in Variable "data_dict" konvertieren
data_dict = dict(data)
# nicht mehr benoetigte Variablen aus Arbeitsspeicher loeschen
del data, response, params, API_URL

# Daten als JSON-Datei speichern
with open('{0}.json'.format(symbol.replace(".", "_")), 'w') as outfile:
    json.dump(data_dict, outfile)

# Dictionary "data_dict" formatiert ausgeben
print(json.dumps(data_dict, indent=2))

{
  "Meta Data": {
    "1. Information": "Daily Prices (open, high, low, close) and Volumes",
    "2. Symbol": "BMW.DE",
    "3. Last Refreshed": "2018-11-16",
    "4. Output Size": "Full size",
    "5. Time Zone": "US/Eastern"
  },
  "Time Series (Daily)": {
    "2018-11-16": {
      "1. open": "74.5600",
      "2. high": "75.1200",
      "3. low": "73.0700",
      "4. close": "73.7400",
      "5. volume": "2427515"
    },
    "2018-11-13": {
      "1. open": "72.3200",
      "2. high": "74.0600",
      "3. low": "72.2000",
      "4. close": "73.9000",
      "5. volume": "2107935"
    },
    "2018-11-12": {
      "1. open": "73.8100",
      "2. high": "73.9600",
      "3. low": "72.2700",
      "4. close": "72.5300",
      "5. volume": "1566238"
    },
    "2018-11-09": {
      "1. open": "73.3300",
      "2. high": "74.0500",
      "3. low": "72.3200",
      "4. close": "73.3600",
      "5. volume": "2200595"
    },
    "2018-11-08": {
      "1. open": "74.3100",
      "2. high": "74

In [3]:
# Dictionary "data_dict" auf inneres "Time Series (Daily)" beschraenken
data_dict = data_dict["Time Series (Daily)"]

# Dictionary "data_dict" formatiert ausgeben
print(json.dumps(data_dict, indent=2))

{
  "2018-11-16": {
    "1. open": "74.5600",
    "2. high": "75.1200",
    "3. low": "73.0700",
    "4. close": "73.7400",
    "5. volume": "2427515"
  },
  "2018-11-13": {
    "1. open": "72.3200",
    "2. high": "74.0600",
    "3. low": "72.2000",
    "4. close": "73.9000",
    "5. volume": "2107935"
  },
  "2018-11-12": {
    "1. open": "73.8100",
    "2. high": "73.9600",
    "3. low": "72.2700",
    "4. close": "72.5300",
    "5. volume": "1566238"
  },
  "2018-11-09": {
    "1. open": "73.3300",
    "2. high": "74.0500",
    "3. low": "72.3200",
    "4. close": "73.3600",
    "5. volume": "2200595"
  },
  "2018-11-08": {
    "1. open": "74.3100",
    "2. high": "74.6000",
    "3. low": "72.8700",
    "4. close": "73.8600",
    "5. volume": "2407914"
  },
  "2018-11-07": {
    "1. open": "74.6100",
    "2. high": "76.1500",
    "3. low": "73.6000",
    "4. close": "74.2600",
    "5. volume": "3911224"
  },
  "2018-11-06": {
    "1. open": "77.2300",
    "2. high": "77.4000",
    

Daten aus "data_dict" in pandas-DataFrame "df" speichern

In [4]:
# Daten aus "data_dict" in pandas-DataFrame "df" speichern
df = pd.DataFrame.from_dict(data_dict, orient='index')
# nicht mehr benoetigte Variable "data_dict" aus Arbeitsspeicher loeschen
del data_dict

# Erste 10 Zeilen des Dataframes "df" ausgeben
df.head(10)

1. open  2. high   3. low 4. close 5. volume
2000-01-03  31.0000  32.0000  28.6600  29.4900   1335338
2000-01-04  29.5000  29.6000  27.7300  28.3000   1564056
2000-01-05  27.5000  28.1000  27.0000  27.7400   1359518
2000-01-06  27.2700  28.4000  27.0000  27.6500   1064746
2000-01-07  27.7600  28.3000  27.2700  27.6000   1575704
2000-01-10  28.2600  28.9900  27.6000  28.7000   1275718
2000-01-11  28.5100  28.7000  27.7400  28.6000   1303046
2000-01-12  28.0100  28.7000  28.0100  28.1900    966988
2000-01-13  28.0000  28.3300  27.0600  27.4000   1614659
2000-01-14  27.8000  28.1500  26.7300  27.2000   2218592

In [5]:
# Spaltennamen umbenennen
df.rename(index=str, columns={"5. volume": "volume", "2. high": "high", "3. low": "low", "4. close": "close", "1. open": "open"}, inplace=True)

# Ausgeben
df.head(0)

Empty DataFrame
Columns: [open, high, low, close, volume]
Index: []

In [6]:
# Index-Format von Zeichenkette zu "datetime" konvertieren
df.index = pd.to_datetime(df.index, format="%Y-%m-%d")

In [7]:
# Datentypen des Dictionarys ausgeben
df.dtypes

open      object
high      object
low       object
close     object
volume    object
dtype: object

In [8]:
# Datentypen zu Zahlenwerten konvertieren
for col in df:
    df[col] = pd.to_numeric(df[col], errors='coerce')

# Datentypen des Dictionarys ausgeben
df.dtypes

open      float64
high      float64
low       float64
close     float64
volume      int64
dtype: object

Daten visualisieren

In [9]:
# Ausgabe im Jupyter Notebook aktivieren
reset_output()
output_notebook()
# Groesse des Fensters 600x300 Pixel, Typ der x-Achse als "datetime" deklarieren
p = figure(plot_width=600, plot_height=300, x_axis_type='datetime')
# Linie hinzufuegen, Index (Datumsangaben) als x-Achse, 
# Schlusskurse "close" als y-Achse, Linienbreite: 2 Pixel
p.line(df.index, df["close"], line_width=2)
# Angeben, welche Zeitangaben je Zoomstufe gezeigt werden sollen
p.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
# Beschriftung der x-Achse um 45° (Bogenmass: pi/4) drehen
p.xaxis.major_label_orientation = pi/4
# Ausgaben
show(p, notebook_handle=True)

Loading BokehJS ...

# Preprocessing (vorbereiten)

Ausreißer entfernen

In [10]:
# Gleitende Standartabweichung
# Spalte "4. close" zu Serie "close_ser" konvertieren
close_ser = pd.Series(df["close"])
# Zahlen in "close_ser" zu float konvertieren
close_ser = pd.to_numeric(close_ser)
# Gleitende Standartabweichung als Variable "std", Laenge des gleitenden Fensters: 5 Einheiten 
# (Werte, ueber die die Standartabweichung gebildet wird)
std = close_ser.rolling(5).std()

In [11]:
# Alle Werte, deren Standartabweichung hoeher als 8 ist, in Serie "entf"
entf = std[std > 8]

# Ausgeben
print(entf)

2000-12-25    15.444415
2000-12-26    18.689300
2000-12-27    18.736688
2000-12-28    18.824638
2000-12-29    19.165125
2001-01-01    15.646182
2018-05-31    38.794899
2018-06-01    38.618131
2018-06-04    38.500841
2018-06-05    38.558459
2018-06-06    38.649362
Name: close, dtype: float64


In [12]:
# Gleitende Standardabweichung "std" Visualisieren
# Ausgabe im Jupyter Notebook aktivieren
reset_output()
output_notebook()
# Groesse des Fensters 600x300 Pixel, Typ der x-Achse als "datetime" deklarieren
p = figure(plot_width=600, plot_height=300, x_axis_type='datetime')
# Linie hinzufuegen, Index (Datumsangaben) als x-Achse, 
# Gleitende Standardabweichung "std" als y-Achse, Linienbreite: 2 Pixel
p.line(df.index, std, line_width=2)
# Angeben, welche Zeitangaben je Zoomstufe gezeigt werden sollen
p.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
# Beschriftung der x-Achse um 45° (Bogenmass: pi/4) drehen
p.xaxis.major_label_orientation = pi/4
# Ausgaben
show(p)

Loading BokehJS ...

In [13]:
# Werte aus Original Dictionary der Spalte "close" an den Positionen aus "entf" mit "NaN" versehen
df["close"].replace(df["close"][entf.index], value=np.NaN, inplace=True)

# Ausgeben
df["close"][entf.index]

2000-12-25   NaN
2000-12-26   NaN
2000-12-27   NaN
2000-12-28   NaN
2000-12-29   NaN
2001-01-01   NaN
2018-05-31   NaN
2018-06-01   NaN
2018-06-04   NaN
2018-06-05   NaN
2018-06-06   NaN
Name: close, dtype: float64

fehlende Werte interpolieren

In [14]:
# fehlende Werte interpolieren
df.interpolate(inplace=True)

# Ausgeben
df["close"][entf.index]

2000-12-25    33.150000
2000-12-26    33.370000
2000-12-27    33.590000
2000-12-28    33.810000
2000-12-29    34.030000
2001-01-01    34.250000
2018-05-31    86.271667
2018-06-01    86.343333
2018-06-04    86.415000
2018-06-05    86.486667
2018-06-06    86.558333
Name: close, dtype: float64

Ueberarbeiteten Aktienkurs ausgeben

In [16]:
# Ausgabe im Jupyter Notebook aktivieren
output_notebook()
output_notebook()
# Groesse des Fensters 600x300 Pixel, Typ der x-Achse als "datetime" deklarieren
p = figure(plot_width=600, plot_height=300, x_axis_type='datetime')
# Linie hinzufuegen, Index (Datumsangaben) als x-Achse, 
# Schlusskurse "close" als y-Achse, Linienbreite: 2 Pixel
p.line(df.index, df["close"], line_width=2)
# Angeben, welche Zeitangaben je Zoomstufe gezeigt werden sollen
p.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
# Beschriftung der x-Achse um 45° (Bogenmass: pi/4) drehen
p.xaxis.major_label_orientation = pi/4
# Ausgaben
show(p, notebook_handle=True)

Loading BokehJS ...

Loading BokehJS ...

Fehler aus allen Spalten entfernen

In [17]:
# Alle Spalten plotten
# Ausgabe im Jupyter Notebook aktivieren
reset_output()
output_notebook()

# Splate "close"
p_close = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Close")
p_close.line(df.index, df["close"], line_width=2, color="#0000FF")
p_close.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_close.xaxis.major_label_orientation = pi/4

# Spalte "high"
p_high = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="High")
p_high.line(df.index, df["high"], line_width=2, color="#006400")
p_high.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_high.xaxis.major_label_orientation = pi/4

# Spalte "low"
p_low = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Low")
p_low.line(df.index, df["low"], line_width=2, color="#DAA520")
p_low.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_low.xaxis.major_label_orientation = pi/4

# Spalte "open"
p_open = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Open")
p_open.line(df.index, df["open"], line_width=2, color="#BA55D3")
p_open.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_open.xaxis.major_label_orientation = pi/4

# Spalte "volume"
p_volume = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Volume")
p_volume.line(df.index, df["volume"], line_width=2, color="#FF4500")
p_volume.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_volume.xaxis.major_label_orientation = pi/4

# Ausgaben
show(bokehcol(p_close, p_high, p_low, p_open, p_volume), notebook_handle=True)

Loading BokehJS ...

In [21]:
# Dataframe "df_test" mit kopierten Inhalt aus "df" erstellen
df_test = df.copy()

# ueber Spalten iterieren
for spalte in df_test:
    # Gleitende Standartabweichung
    # Spalte "4. close" zu Serie "temp_serie" konvertieren
    temp_serie = pd.Series(df_test[spalte])
    # Zahlen in "temp_serie" zu float konvertieren
    temp_serie = pd.to_numeric(temp_serie)
    # Gleitende Standartabweichung als Variable "std", Laenge des gleitenden Fensters: 5 Einheiten 
    # (Werte, ueber die die Standartabweichung gebildet wird)
    std = temp_serie.rolling(5).std()
    # Nicht mehr benoetigte Variable "temp_serie" aus Arbeitsspeicher entfernen
    del temp_serie
    # Alle Werte, deren Standartabweichung hoeher als 8 ist, in Serie "entf"
    entf = std[std > 8]
    # Nicht mehr benoetigte Variable "std" aus Arbeitsspeicher entfernen
    del std
    # Werte aus Original Dictionary der iterierten Spalte an den Positionen aus "entf" mit "NaN" versehen
    df_test[spalte].replace(df_test[spalte][entf.index], value=np.NaN, inplace=True)
    # Nicht mehr benoetigte Variable "entf" aus Arbeitsspeicher entfernen
    del entf
    
# Nicht mehr benoetigte Variable "spalte" aus Arbeitsspeicher entfernen
del spalte
# fehlende Werte interpolieren
df_test.interpolate(inplace=True)

In [22]:
# Alle Spalten plotten
# Ausgabe im Jupyter Notebook aktivieren
reset_output()
output_notebook()

# Splate "close"
p_close = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Close")
p_close.line(df_test.index, df_test["close"], line_width=2, color="#0000FF")
p_close.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_close.xaxis.major_label_orientation = pi/4

# Spalte "high"
p_high = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="High")
p_high.line(df_test.index, df_test["high"], line_width=2, color="#006400")
p_high.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_high.xaxis.major_label_orientation = pi/4

# Spalte "low"
p_low = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Low")
p_low.line(df_test.index, df_test["low"], line_width=2, color="#DAA520")
p_low.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_low.xaxis.major_label_orientation = pi/4

# Spalte "open"
p_open = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Open")
p_open.line(df_test.index, df_test["open"], line_width=2, color="#BA55D3")
p_open.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_open.xaxis.major_label_orientation = pi/4

# Spalte "volume"
p_volume = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Volume")
p_volume.line(df_test.index, df_test["volume"], line_width=2, color="#FF4500")
p_volume.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_volume.xaxis.major_label_orientation = pi/4

# Ausgaben
show(bokehcol(p_close, p_high, p_low, p_open, p_volume), notebook_handle=True)

Loading BokehJS ...

In [23]:
# Wie zu sehen ist, kann die Behandlung des Handelsvolumen nicht 
# mit der Massnahme der Standardabweichung vorgenommen werden,
# daher wird die Spalte "volume" aus der Iteration ausgeschlossen

# ueber Spalten iterieren
for spalte in df:
    # Spalte "volume" ausschliessen
    if spalte != "volume":
        # Gleitende Standartabweichung
        # Spalte "4. close" zu Serie "temp_serie" konvertieren
        temp_serie = pd.Series(df[spalte])
        # Zahlen in "temp_serie" zu float konvertieren
        temp_serie = pd.to_numeric(temp_serie)
        # Gleitende Standartabweichung als Variable "std", Laenge des gleitenden Fensters: 5 Einheiten 
        # (Werte, ueber die die Standartabweichung gebildet wird)
        std = temp_serie.rolling(5).std()
        # Nicht mehr benoetigte Variable "temp_serie" aus Arbeitsspeicher entfernen
        del temp_serie
        # Alle Werte, deren Standartabweichung hoeher als 8 ist, in Serie "entf"
        entf = std[std > 8]
        # Nicht mehr benoetigte Variable "std" aus Arbeitsspeicher entfernen
        del std
        # Werte aus Original Dictionary der iterierten Spalte an den Positionen aus "entf" mit "NaN" versehen
        df[spalte].replace(df[spalte][entf.index], value=np.NaN, inplace=True)
        # Nicht mehr benoetigte Variable "entf" aus Arbeitsspeicher entfernen
        del entf
    
# Nicht mehr benoetigte Variable "spalte" aus Arbeitsspeicher entfernen
del spalte
# fehlende Werte interpolieren
df.interpolate(inplace=True)

In [24]:
# Alle Spalten plotten
# Ausgabe im Jupyter Notebook aktivieren
reset_output()
output_notebook()

# Splate "close"
p_close = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Close")
p_close.line(df.index, df["close"], line_width=2, color="#0000FF")
p_close.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_close.xaxis.major_label_orientation = pi/4

# Spalte "high"
p_high = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="High")
p_high.line(df.index, df["high"], line_width=2, color="#006400")
p_high.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_high.xaxis.major_label_orientation = pi/4

# Spalte "low"
p_low = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Low")
p_low.line(df.index, df["low"], line_width=2, color="#DAA520")
p_low.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_low.xaxis.major_label_orientation = pi/4

# Spalte "open"
p_open = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Open")
p_open.line(df.index, df["open"], line_width=2, color="#BA55D3")
p_open.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_open.xaxis.major_label_orientation = pi/4

# Spalte "volume"
p_volume = figure(plot_width=600, plot_height=300, x_axis_type='datetime', title="Volume")
p_volume.line(df.index, df["volume"], line_width=2, color="#FF4500")
p_volume.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
p_volume.xaxis.major_label_orientation = pi/4

# Ausgaben
show(bokehcol(p_close, p_high, p_low, p_open, p_volume), notebook_handle=True)

Loading BokehJS ...

In [26]:
# Werte aus Original Dictionary der Spalte "close" an den Positionen aus "entf" mit "NaN" versehen
df["volume"].replace(0, value=np.NaN, inplace=True)

In [28]:
df["volume"][df["volume"] == np.NaN]

Series([], Name: volume, dtype: float64)

In [31]:
df["volume"].isnull().sum()

76

In [33]:
null_columns = df["volume"].isnull()

In [37]:
print(df["volume"][null_columns].head(10))

2000-04-21   NaN
2000-04-24   NaN
2000-05-01   NaN
2000-05-09   NaN
2000-07-07   NaN
2000-07-13   NaN
2000-09-13   NaN
2000-10-03   NaN
2000-10-13   NaN
2000-10-16   NaN
Name: volume, dtype: float64


In [38]:
# fehlende Werte interpolieren
df.interpolate(inplace=True)

In [39]:
print(df["volume"][null_columns].head(10))

2000-04-21    1.704300e+06
2000-04-24    1.220103e+06
2000-05-01    3.861794e+06
2000-05-09    1.589246e+06
2000-07-07    2.164330e+06
2000-07-13    1.908992e+06
2000-09-13    7.152985e+05
2000-10-03    2.425540e+06
2000-10-13    1.736941e+06
2000-10-16    1.609622e+06
Name: volume, dtype: float64


In [43]:
# Ausgabe im Jupyter Notebook aktivieren
output_notebook()
output_notebook()
# Groesse des Fensters 600x300 Pixel, Typ der x-Achse als "datetime" deklarieren
p = figure(plot_width=600, plot_height=300, x_axis_type='datetime')
# Linie hinzufuegen, Index (Datumsangaben) als x-Achse, 
# Schlusskurse "close" als y-Achse, Linienbreite: 2 Pixel
p.line(df.index, df["volume"], line_width=2, color="#FF4500")
# Angeben, welche Zeitangaben je Zoomstufe gezeigt werden sollen
p.xaxis.formatter = DatetimeTickFormatter(
    hourmin=['%H:%M'],
    hours=["%d.%m %H:%M"],
    days=["%d.%m."],
    months=["%d.%m.%Y"],
    years=["%m/%Y"],
)
# Beschriftung der x-Achse um 45° (Bogenmass: pi/4) drehen
p.xaxis.major_label_orientation = pi/4

p.left[0].formatter.use_scientific = False

# Ausgaben
show(p, notebook_handle=True)

Loading BokehJS ...

Loading BokehJS ...